In [1]:
import os
import copy
import random
import gym
import pickle

import numpy as np
import pandas as pd
import tensorflow as tf
tf.keras.backend.set_floatx('float32')

from itertools import permutations
from sklearn.model_selection import KFold, GridSearchCV

from multiprocessing import set_start_method
import multiprocessing as mp

path = os.path.abspath('..')
if path not in sys.path:
    sys.path.append(path)

from peal.agents.default_config import DEFAULT_CONFIG as config
# from peal.agents.dqn import DQNAgent
from peal.agents.qr_dqn import QuantileAgent
# from peal.agents.multi_head_dqn import MultiHeadDQNAgent
# from peal.agents.discrete_bcq import DiscreteBCQAgent

from peal.algos.kfold import CVS, KFoldCV
from peal.algos.advantage_learner import AdvantageLearner
from peal.algos.behavior_cloning import BehaviorCloning
from peal.algos.density_ratio import VisitationRatioModel
from peal.algos.fqe import FQE

def one_step(seed):
    np.random.seed(seed)
    tf.random.set_seed(seed)
    
    path = './data/mh/qr_dqn/trajs_mh.pkl'
    nfolds = 5
    n_splits = 5
    ckpts = (np.arange(10) + 1)*1000
    
    num_actions = 5
    # configures
    config['online'] = False
    config['lr'] = 5e-4
    config['decay_steps'] = 50000
    config['max_training_steps'] = 10000
    config['training_steps_to_checkpoint'] = 1000
    config['training_steps_to_eval'] = 100000
    config['hiddens'] = [64,64]
    config['double'] = False
    config['dueling'] = False

    index = pd.MultiIndex.from_product([np.arange(nfolds), ckpts])
    columns = ['dqn',  'peal']
    rets = pd.DataFrame(index=index, columns=columns)

    print('-'*20, 'start', '-'*20)
    cvs = CVS(path, n_splits=nfolds, random_state=seed)
    cvs.split()
    for fold in range(nfolds):
        train_path = cvs.train_paths[fold] + 'trajs.pkl'
        kf = KFoldCV(train_path, n_trajs=None, n_splits=n_splits, shuffle=False, random_state=seed)
        kf.split()

        print('-'*20, 'training agent', '-'*20)
        # agent
        config['persistent_directory'] = kf.agent_path
        config['checkpoint_path'] = kf.ckpt_path
        agent = QuantileAgent(num_actions=num_actions, config=config)
        agent.learn()

        print('-'*20, 'training agents', '-'*20)
        # agent_1, ..., agent_K
        for idx in range(kf.n_splits):
            config_idx = copy.deepcopy(config)
            config_idx['persistent_directory'] = kf.agent_paths[idx]
            config_idx['checkpoint_path'] = kf.ckpt_paths[idx]
            agent_idx = QuantileAgent(num_actions=num_actions, config=config_idx)
            agent_idx.learn()

        # fitted q evaluation
        test_path = cvs.test_paths[fold] + 'trajs.pkl'
        with open(test_path, 'rb') as f:
            trajs = pickle.load(f)

        print('-'*20, 'behavior cloning', '-'*20)
        # behavior cloning
        bc = BehaviorCloning(num_actions=num_actions)
        states  = np.array([transition[0] for traj in kf.trajs for transition in traj])
        actions = np.array([transition[1] for traj in kf.trajs for transition in traj])
        bc.train(states, actions)

        for ckpt in ckpts:
            print('-'*20, 'ckpt: ', ckpt, '-'*20)
            agent = QuantileAgent(num_actions=num_actions, config=config)
            agent.load(kf.ckpt_path + 'offline_qr_dqn_{}.ckpt'.format(ckpt))

            agents = []
            for idx in range(kf.n_splits):
                config_idx = copy.deepcopy(config)
                config_idx['persistent_directory'] = kf.agent_paths[idx]
                config_idx['checkpoint_path'] = kf.ckpt_paths[idx]
                agent_idx = QuantileAgent(num_actions=num_actions, config=config_idx)
                agent_idx.load(kf.ckpt_paths[idx] + 'offline_qr_dqn_{}.ckpt'.format(ckpt))
                agents.append(agent_idx)
            states, qvalues, qtildes = kf.update_q(agents, bc)

            print('-'*20, 'adv learner', '-'*20)
#             advs1 = qvalues - qvalues.mean(axis=1, keepdims=True)
#             agent1 = AdvantageLearner(num_actions=num_actions)
#             agent1._train(states, advs1)
            
            advs2 = qtildes - qtildes.mean(axis=1, keepdims=True)
            agent2 = AdvantageLearner(num_actions=num_actions)
            agent2._train(states, advs2)

            print('-'*20, 'fqe on dqn & peal', '-'*20)
            fqe_dqn = FQE(agent.greedy_actions, num_actions=num_actions, activation='tanh', hiddens=config['hiddens'], max_iter=100, eps=0.0015)
            fqe_dqn.train(trajs)
#             fqe_dml = FQE(agent1.greedy_actions, num_actions=num_actions)
#             fqe_dml.train(trajs)
            fqe_peal = FQE(agent2.greedy_actions, num_actions=num_actions, activation='tanh', hiddens=config['hiddens'], max_iter=100, eps=0.0015)
            fqe_peal.train(trajs)

            rets.loc[(fold, ckpt), 'dqn'] = fqe_dqn.values
#             rets.loc[(fold, ckpt), 'dml'] = fqe_dml.values
            rets.loc[(fold, ckpt), 'peal'] = fqe_peal.values
            
    return rets

In [2]:
save_path = './data/mh/qr_dqn/'
pool = mp.Pool(5)
rets = pool.map(one_step, range(5))
pool.close()

with open(save_path + 'rets_qr_dqn_mh.pkl', 'wb') as f:
    pickle.dump(rets, f)

------------------------------------------------------------ ----------------------------------------start     startstartstartstart--------------------    
--------------------------------------------------------------------------------



-------------------- training agent ---------------------------------------- -------------------- training agent
training agent -------------------- 
--------------------
-------------------- training agent --------------------
-------------------- training agent --------------------
Loaded trajectories from load path: /home/jupyt/leyuan/SUPRL/data/mh/qr_dqn/tmp/209652396/fold0/train/agent/trajs.pkl!
Refresh buffer every 1000000 sampling!
Loaded trajectories from load path: /home/jupyt/leyuan/SUPRL/data/mh/qr_dqn/tmp/717354021/fold0/train/agent/trajs.pkl!
Refresh buffer every 1000000 sampling!
Loaded trajectories from load path: /home/jupyt/leyuan/SUPRL/data/mh/qr_dqn/tmp/798842024/fold0/train/agent/trajs.pkl!
Refresh buffer every 1000000 sampling!Lo



saving model weights at /home/jupyt/leyuan/SUPRL/data/mh/qr_dqn/tmp/932136058/fold0/train/agent/ckpt/offline_qr_dqn_1000.ckpt
saving model weights at /home/jupyt/leyuan/SUPRL/data/mh/qr_dqn/tmp/717354021/fold0/train/agent/ckpt/offline_qr_dqn_1000.ckpt
saving model weights at /home/jupyt/leyuan/SUPRL/data/mh/qr_dqn/tmp/798842024/fold0/train/agent/ckpt/offline_qr_dqn_1000.ckpt
saving model weights at /home/jupyt/leyuan/SUPRL/data/mh/qr_dqn/tmp/209652396/fold0/train/agent/ckpt/offline_qr_dqn_1000.ckpt
saving model weights at /home/jupyt/leyuan/SUPRL/data/mh/qr_dqn/tmp/218175338/fold0/train/agent/ckpt/offline_qr_dqn_1000.ckpt
saving model weights at /home/jupyt/leyuan/SUPRL/data/mh/qr_dqn/tmp/932136058/fold0/train/agent/ckpt/offline_qr_dqn_2000.ckpt
saving model weights at /home/jupyt/leyuan/SUPRL/data/mh/qr_dqn/tmp/717354021/fold0/train/agent/ckpt/offline_qr_dqn_2000.ckpt
saving model weights at /home/jupyt/leyuan/SUPRL/data/mh/qr_dqn/tmp/218175338/fold0/train/agent/ckpt/offline_qr_dqn_



If you intended to run this layer in float32, you can safely ignore this warning. If in doubt, this warning is likely only an issue if you are porting a TensorFlow 1.X model to TensorFlow 2.

To change all layers to have dtype float64 by default, call `tf.keras.backend.set_floatx('float64')`. To change just this layer, pass dtype='float64' to the layer constructor. If you are the author of this layer, you can disable autocasting by passing autocast=False to the base Layer constructor.

saving model weights at /home/jupyt/leyuan/SUPRL/data/mh/qr_dqn/tmp/798842024/fold0/train/agent/ckpt/offline_qr_dqn_10000.ckpt
-------------------- training agents --------------------
Loaded trajectories from load path: /home/jupyt/leyuan/SUPRL/data/mh/qr_dqn/tmp/798842024/fold0/train/agent0/trajs0.pkl!
Refresh buffer every 1000000 sampling!

If you intended to run this layer in float32, you can safely ignore this warning. If in doubt, this warning is likely only an issue if you are porting a TensorFl


saving model weights at /home/jupyt/leyuan/SUPRL/data/mh/qr_dqn/tmp/218175338/fold0/train/agent0/ckpt/offline_qr_dqn_10000.ckpt
Loaded trajectories from load path: /home/jupyt/leyuan/SUPRL/data/mh/qr_dqn/tmp/218175338/fold0/train/agent1/trajs1.pkl!
Refresh buffer every 1000000 sampling!

If you intended to run this layer in float32, you can safely ignore this warning. If in doubt, this warning is likely only an issue if you are porting a TensorFlow 1.X model to TensorFlow 2.

To change all layers to have dtype float64 by default, call `tf.keras.backend.set_floatx('float64')`. To change just this layer, pass dtype='float64' to the layer constructor. If you are the author of this layer, you can disable autocasting by passing autocast=False to the base Layer constructor.


If you intended to run this layer in float32, you can safely ignore this warning. If in doubt, this warning is likely only an issue if you are porting a TensorFlow 1.X model to TensorFlow 2.

To change all layers to ha

Refresh buffer every 1000000 sampling!

If you intended to run this layer in float32, you can safely ignore this warning. If in doubt, this warning is likely only an issue if you are porting a TensorFlow 1.X model to TensorFlow 2.

To change all layers to have dtype float64 by default, call `tf.keras.backend.set_floatx('float64')`. To change just this layer, pass dtype='float64' to the layer constructor. If you are the author of this layer, you can disable autocasting by passing autocast=False to the base Layer constructor.


If you intended to run this layer in float32, you can safely ignore this warning. If in doubt, this warning is likely only an issue if you are porting a TensorFlow 1.X model to TensorFlow 2.

To change all layers to have dtype float64 by default, call `tf.keras.backend.set_floatx('float64')`. To change just this layer, pass dtype='float64' to the layer constructor. If you are the author of this layer, you can disable autocasting by passing autocast=False to the ba

...


-------------------- adv learner --------------------
-----iteration:  90 target diff:  0.002369625715816651 values:  -44.37178 ----- 

-----iteration:  91 target diff:  0.0022981778584396403 values:  -44.33488 ----- 

-----iteration:  92 target diff:  0.0020800404247141467 values:  -44.28493 ----- 

-----iteration:  93 target diff:  0.002261776511632984 values:  -44.30873 ----- 

-----iteration:  94 target diff:  0.0025143087673366905 values:  -44.269554 ----- 

-------------------- fqe on dqn & sale --------------------
-----iteration:  95 target diff:  0.001979543154811761 values:  -44.221466 ----- 

-----iteration:  96 target diff:  0.0022134443498528734 values:  -44.241314 ----- 

-----iteration:  97 target diff:  0.002517223688444855 values:  -44.19477 ----- 

-----iteration:  98 target diff:  0.0020159615256038293 values:  -44.1442 ----- 

-----iteration:  99 target diff:  0.0026311395593066784 values:  -44.160175 ----- 

-------------------- ckpt:  10000 --------------------
L



If you intended to run this layer in float32, you can safely ignore this warning. If in doubt, this warning is likely only an issue if you are porting a TensorFlow 1.X model to TensorFlow 2.

To change all layers to have dtype float64 by default, call `tf.keras.backend.set_floatx('float64')`. To change just this layer, pass dtype='float64' to the layer constructor. If you are the author of this layer, you can disable autocasting by passing autocast=False to the base Layer constructor.


If you intended to run this layer in float32, you can safely ignore this warning. If in doubt, this warning is likely only an issue if you are porting a TensorFlow 1.X model to TensorFlow 2.

To change all layers to have dtype float64 by default, call `tf.keras.backend.set_floatx('float64')`. To change just this layer, pass dtype='float64' to the layer constructor. If you are the author of this layer, you can disable autocasting by passing autocast=False to the base Layer constructor.


If you intende

-----iteration:  6 target diff:  0.0026302219202583134 values:  -46.935555 ----- 

-----iteration:  7 target diff:  0.0021060714115459585 values:  -46.94107 ----- 

-----iteration:  8 target diff:  0.0028129102344645303 values:  -46.9157 ----- 

-----iteration:  9 target diff:  0.002268807365032187 values:  -46.895542 ----- 

-------------------- fqe on dqn & sale --------------------
-----iteration:  10 target diff:  0.0019920933416990045 values:  -46.901665 ----- 

-----iteration:  11 target diff:  0.002178767776117465 values:  -46.886456 ----- 

-----iteration:  12 target diff:  0.0018113432495567526 values:  -46.83901 ----- 

-----iteration:  13 target diff:  0.0018958449356414402 values:  -46.987797 ----- 

-----iteration:  14 target diff:  0.0033798011239032527 values:  -46.988834 ----- 

-----iteration:  15 target diff:  0.0024717445412617113 values:  -46.96253 ----- 


If you intended to run this layer in float32, you can safely ignore this warning. If in doubt, this warning is


-----iteration:  36 target diff:  0.0017939932093525045 values:  -46.442997 ----- 

-----iteration:  0 target diff:  0.9194654562756657 values:  -58.135277 ----- 

-----iteration:  37 target diff:  0.002205587102261255 values:  -46.492046 ----- 

-----iteration:  1 target diff:  0.0012904812112667465 values:  -58.144226 ----- 

-----iteration:  38 target diff:  0.002565399628551233 values:  -46.51122 ----- 

-----iteration:  39 target diff:  0.0021316931858611616 values:  -46.56318 ----- 

-----iteration:  40 target diff:  0.0022330980710296797 values:  -46.608135 ----- 

-----iteration:  41 target diff:  0.0025433783292307596 values:  -46.63418 ----- 

-----iteration:  42 target diff:  0.002209086098682238 values:  -46.59961 ----- 

-----iteration:  43 target diff:  0.0022542770058833913 values:  -46.536427 ----- 

-----iteration:  44 target diff:  0.0018381668779625894 values:  -46.579613 ----- 


If you intended to run this layer in float32, you can safely ignore this warning. If i

-----iteration:  72 target diff:  0.002096421032146848 values:  -42.93005 ----- 

-----iteration:  73 target diff:  0.0019360762650014152 values:  -42.928867 ----- 

-----iteration:  74 target diff:  0.0021462466407715882 values:  -42.94437 ----- 

-----iteration:  75 target diff:  0.002315560535201298 values:  -42.991745 ----- 

-----iteration:  76 target diff:  0.002434261047962204 values:  -43.03884 ----- 

-----iteration:  77 target diff:  0.0021943066160313007 values:  -42.974964 ----- 

-----iteration:  78 target diff:  0.0022744634566832195 values:  -42.927116 ----- 

-----iteration:  79 target diff:  0.001942316255185676 values:  -42.931206 ----- 

-----iteration:  80 target diff:  0.0019252762847657926 values:  -42.96533 ----- 

-----iteration:  81 target diff:  0.001954910092565119 values:  -42.994194 ----- 

-----iteration:  82 target diff:  0.001819917836896095 values:  -42.958572 ----- 

-----iteration:  83 target diff:  0.0019459445438939533 values:  -42.921597 ----- 

--